## Install Dependencies

In [1]:
! pip install -U datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 3.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 4.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 6.2 MB/s eta 0:00:00


In [2]:
import pandas as pd
from datasets import load_dataset, DatasetDict
from huggingface_hub import notebook_login

## Preprocess data

In [4]:
df = pd.read_csv("cleaned_data.csv", usecols=['text', 'sentiment'])
df.head()

text sentiment
0  If you decide to eat here, just be aware it is...   Neutral
1  I am a long term frequent customer of this est...  Negative
2  Loved this tour! I grabbed a groupon and the p...  Positive
3  Love going here for happy hour or dinner!  Gre...  Positive
4  Great staff always helps and always nice. Alwa...  Positive

In [5]:
df['sentiment'].value_counts()

sentiment
Positive    101121
Negative     36346
Neutral      16846
Name: count, dtype: int64

In [6]:
def sentiment_to_int(sentiment: str) -> int:
    if(sentiment.lower() == "negative"):
        return 0
    if(sentiment.lower() == "neutral"):
        return 1
    if(sentiment.lower() == "positive"):
        return 2
    raise Exception(f"{sentiment} is not a valid value")


In [7]:
df['sentiment'] = df['sentiment'].apply(sentiment_to_int)
df.head()

text  sentiment
0  If you decide to eat here, just be aware it is...          1
1  I am a long term frequent customer of this est...          0
2  Loved this tour! I grabbed a groupon and the p...          2
3  Love going here for happy hour or dinner!  Gre...          2
4  Great staff always helps and always nice. Alwa...          2

In [8]:
df.rename(columns={"sentiment": "label"}, inplace=True)
df.head()

text  label
0  If you decide to eat here, just be aware it is...      1
1  I am a long term frequent customer of this est...      0
2  Loved this tour! I grabbed a groupon and the p...      2
3  Love going here for happy hour or dinner!  Gre...      2
4  Great staff always helps and always nice. Alwa...      2

In [9]:
split_index = int(0.75 * len(df))
train_df, test_df = df[:split_index], df[split_index:]
train_df.shape, test_df.shape

((115734, 2), (38579, 2))

## Save the data

In [10]:
train_df.to_csv('train.csv', index=False)
test_df.to_csv('test.csv', index=False)

## Uploading to Hub

In [11]:
notebook_login()

In [12]:
yelp_dataset = DatasetDict.from_csv({'train': 'train.csv', 'test': 'test.csv'})

Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

In [13]:
yelp_dataset.push_to_hub("noahnsimbe/yelp-dataset")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/116 [00:00<?, ?ba/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/39 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/5.01k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/datasets/noahnsimbe/yelp-dataset/commit/999b45ff6e66f5a4af360076c11b4f9ff4aa8215', commit_message='Upload dataset', commit_description='', oid='999b45ff6e66f5a4af360076c11b4f9ff4aa8215', pr_url=None, pr_revision=None, pr_num=None)

## Testing

In [14]:
yelp_dataset = load_dataset("noahnsimbe/yelp-dataset")

Generating train split:   0%|          | 0/115734 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/38579 [00:00<?, ? examples/s]

In [15]:
yelp_train_df = pd.DataFrame(yelp_dataset['train'])
yelp_test_df = pd.DataFrame(yelp_dataset['test'])

In [16]:
yelp_train_df.head()

text  label
0  If you decide to eat here, just be aware it is...      1
1  I am a long term frequent customer of this est...      0
2  Loved this tour! I grabbed a groupon and the p...      2
3  Love going here for happy hour or dinner!  Gre...      2
4  Great staff always helps and always nice. Alwa...      2

In [17]:
yelp_test_df.head()

text  label
0  This place is still pretty new but you'd never...      2
1  For the experience sure, for the amount it cos...      1
2  Headed to Tucson for grandma's 97th birthday. ...      2
3  The service at this place was terrible! I don'...      0
4  Decent pizza, iced tea, fresh salads.  Booths ...      2

In [19]:
yelp_test_df['label'].value_counts()


label
2    23678
0    11128
1     3773
Name: count, dtype: int64

In [20]:
yelp_train_df['label'].value_counts()

label
2    77443
0    25218
1    13073
Name: count, dtype: int64